In [1]:
import pandas as pd
from bokeh.plotting import figure, output_notebook, show
import datashader as ds
from datashader.bokeh_ext import InteractiveImage
from functools import partial
from datashader.utils import export_image
from datashader.colors import colormap_select, Greys9, Hot, viridis, inferno
from IPython.core.display import HTML, display
from datashader import transfer_functions as tf
from datashader.colors import Greys9

Load in the Float and Land Data

In [2]:
df_float = pd.read_pickle("float_coords.pkl")
df_land = pd.read_pickle("land_coords.pkl")

Configure Plot Parameters ( based off of [this example](https://github.com/bokeh/datashader/blob/master/examples/nyc_taxi.ipynb) )

In [3]:
output_notebook()
DOMAIN = x_range, y_range = ((-280,80), (-81,65))
plot_width  = int(900)
plot_height = int(plot_width//1.4)
options = dict(line_color=None, fill_color='blue', size=5)
def base_plot(tools='pan,wheel_zoom,reset',plot_width=plot_width, plot_height=plot_height, **plot_args):
    p = figure(tools=tools, plot_width=plot_width, plot_height=plot_height,
        x_range=x_range, y_range=y_range, outline_line_color=None,
        min_border=0, min_border_left=0, min_border_right=0,
        min_border_top=0, min_border_bottom=0, **plot_args)
    
    p.axis.visible = True
    p.xgrid.grid_line_color = None
    p.ygrid.grid_line_color = None
    return p

Loading BokehJS ...

Configure and Build the Interactive Image

In [4]:
background = "white"
export = partial(export_image, export_path="export", background=background)
cm = partial(colormap_select, reverse=(background=="white"))

def create_image(x_range, y_range, w=plot_width, h=plot_height):
    cvs = ds.Canvas(plot_width=w, plot_height=h, x_range=x_range, y_range=y_range)
    agg_land = cvs.points(df_land, 'land_x', 'land_y')
    agg_ocean = cvs.points(df_float, 'float_x', 'float_y')
    img_land = tf.shade(agg_land, cmap=['lightgreen', 'darkgreen'], how='eq_hist')
    img_ocean = tf.shade(agg_ocean,cmap=['lightblue', 'darkblue'], how='eq_hist')
    img_combined = tf.stack(img_ocean, img_land)
    return tf.dynspread(img_combined, threshold=.8, max_px=40)

p = base_plot(background_fill_color=background)
InteractiveImage(p, create_image)